In [1]:
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler, LabelEncoder
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense
from tensorflow.keras.utils import to_categorical

In [3]:
df = pd.read_csv("music_genre.csv")
df

instance_id           artist_name                track_name  \
0          32894.0              Röyksopp      Röyksopp's Night Out   
1          46652.0  Thievery Corporation          The Shining Path   
2          30097.0        Dillon Francis                 Hurricane   
3          62177.0              Dubloadz                     Nitro   
4          24907.0           What So Not          Divide & Conquer   
...            ...                   ...                       ...   
50000      58878.0                 BEXEY                  GO GETTA   
50001      43557.0             Roy Woods       Drama (feat. Drake)   
50002      39767.0                Berner  Lovin' Me (feat. Smiggz)   
50003      57944.0             The-Dream         Shawty Is Da Shit   
50004      63470.0     Naughty By Nature            Hip Hop Hooray   

       popularity  acousticness  danceability  duration_ms  energy  \
0            27.0       0.00468         0.652         -1.0   0.941   
1            31.0       0.01270         0.622     218293.0   0.890   
2            28.0       0.00306         0.620     215613.0   0.755   
3            34.0       0.02540         0.774     166875.0   0.700   
4            32.0       0.00465         0.638     222369.0   0.587   
...           ...           ...           ...          ...     ...   
50000        59.0       0.03340         0.913         -1.0   0.574   
50001        72.0       0.15700         0.709     251860.0   0.362   
50002        51.0       0.00597         0.693     189483.0   0.763   
50003        65.0       0.08310         0.782     262773.0   0.472   
50004        67.0       0.10200         0.862     267267.0   0.642   

       instrumentalness key  liveness  loudness   mode  speechiness  \
0               0.79200  A#     0.115    -5.201  Minor       0.0748   
1               0.95000   D     0.124    -7.043  Minor       0.0300   
2               0.01180  G#     0.534    -4.617  Major       0.0345   
3               0.00253  C#     0.157    -4.498  Major       0.2390   
4               0.90900  F#     0.157    -6.266  Major       0.0413   
...                 ...  ..       ...       ...    ...          ...   
50000           0.00000  C#     0.119    -7.022  Major       0.2980   
50001           0.00000   B     0.109    -9.814  Major       0.0550   
50002           0.00000   D     0.143    -5.443  Major       0.1460   
50003           0.00000   G     0.106    -5.016  Minor       0.0441   
50004           0.00000  F#     0.272   -13.652  Minor       0.1010   

                    tempo obtained_date  valence music_genre  
0                 100.889         4-Apr    0.759  Electronic  
1      115.00200000000001         4-Apr    0.531  Electronic  
2                 127.994         4-Apr    0.333  Electronic  
3                 128.014         4-Apr    0.270  Electronic  
4                 145.036         4-Apr    0.323  Electronic  
...                   ...           ...      ...         ...  
50000   98.02799999999999         4-Apr    0.330     Hip-Hop  
50001  122.04299999999999         4-Apr    0.113     Hip-Hop  
50002             131.079         4-Apr    0.395     Hip-Hop  
50003   75.88600000000001         4-Apr    0.354     Hip-Hop  
50004   99.20100000000001         4-Apr    0.765     Hip-Hop  

[50005 rows x 18 columns]

In [4]:
df.drop('mode', axis=1, inplace=True)

In [5]:
le_key = LabelEncoder()
df["key"] = le_key.fit_transform(df["key"])

df["tempo"] = pd.to_numeric(df["tempo"], errors="coerce")
df.dropna(subset=["tempo"], inplace=True)

In [6]:
features = [
    "popularity",
    "acousticness",
    "danceability",
    "duration_ms",
    "energy",
    "instrumentalness",
    "key",
    "liveness",
    "loudness",
    "speechiness",
    "tempo",
    "valence",
]

target = "music_genre"

X = df[features]
y = df[target]

In [7]:
le_genre = LabelEncoder()
y_encoded = le_genre.fit_transform(y)
y_categorical = to_categorical(y_encoded)

In [8]:
X_temp, X_real_test, y_temp, y_real_test = train_test_split(
    X, y_categorical, test_size=0.2, random_state=42
)


X_train, X_val, y_train, y_val = train_test_split(
    X_temp, y_temp, test_size=0.25, random_state=42
)

In [9]:
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_val_scaled = scaler.transform(X_val)
X_real_test_scaled = scaler.transform(X_real_test)

In [10]:
model = Sequential()
model.add(Dense(128, input_dim=X_train_scaled.shape[1], activation="relu"))
model.add(Dense(64, activation="relu"))
model.add(Dense(32, activation="relu"))
model.add(Dense(y_categorical.shape[1], activation="softmax"))

In [11]:
model.compile(loss="categorical_crossentropy", optimizer="adam", metrics=["accuracy"])

In [12]:
history = model.fit(
    X_train_scaled,
    y_train,
    epochs=25,
    validation_data=(X_val_scaled, y_val),
)

Epoch 1/25
845/845 [==============================] - 3s 3ms/step - loss: 1.3402 - accuracy: 0.4904 - val_loss: 1.2166 - val_accuracy: 0.5253
Epoch 2/25
845/845 [==============================] - 2s 2ms/step - loss: 1.1871 - accuracy: 0.5425 - val_loss: 1.1755 - val_accuracy: 0.5500
Epoch 3/25
845/845 [==============================] - 2s 2ms/step - loss: 1.1550 - accuracy: 0.5514 - val_loss: 1.1548 - val_accuracy: 0.5612
Epoch 4/25
845/845 [==============================] - 2s 3ms/step - loss: 1.1364 - accuracy: 0.5583 - val_loss: 1.1337 - val_accuracy: 0.5610
Epoch 5/25
845/845 [==============================] - 4s 5ms/step - loss: 1.1213 - accuracy: 0.5631 - val_loss: 1.1298 - val_accuracy: 0.5662
Epoch 6/25
845/845 [==============================] - 4s 5ms/step - loss: 1.1085 - accuracy: 0.5717 - val_loss: 1.1364 - val_accuracy: 0.5612
Epoch 7/25
845/845 [==============================] - 5s 5ms/step - loss: 1.0970 - accuracy: 0.5714 - val_loss: 1.1236 - val_accuracy: 0.5627
Epoch 

In [13]:
real_test_loss, real_test_accuracy = model.evaluate(X_real_test_scaled, y_real_test)
print(f"Real Test Accuracy: {real_test_accuracy:.4f}")

282/282 [==============================] - 0s 2ms/step - loss: 1.1065 - accuracy: 0.5704
Real Test Accuracy: 0.5704


In [14]:
df[df['track_name'] == "Ron's Theme"]

instance_id  artist_name   track_name  popularity  acousticness  \
11331      41965.0  empty_field  Ron's Theme        36.0         0.938   

       danceability  duration_ms  energy  instrumentalness  key  liveness  \
11331          0.41      86093.0  0.0117             0.802    3      0.11   

       loudness  speechiness   tempo obtained_date  valence music_genre  
11331   -28.914       0.0419  79.948         4-Apr   0.0567        Jazz

In [15]:
import plotly.express as px
from sklearn.decomposition import PCA

# Apply PCA to reduce the dimensionality of the features to 2D
pca = PCA(n_components=2, random_state=42)
X_pca = pca.fit_transform(X)

# Create a DataFrame with the embedded points and genre labels
pca_df = pd.DataFrame({
    'PCA Dimension 1': X_pca[:, 0],
    'PCA Dimension 2': X_pca[:, 1],
    'Genre': df['music_genre'],
    'Track Name': df['track_name']
})

# Create an interactive scatter plot with hover information using Plotly Express
fig = px.scatter(pca_df, x='PCA Dimension 1', y='PCA Dimension 2', color='Genre', hover_data=['Genre', 'Track Name'])
fig.update_layout(title='PCA Visualization of Music Genres Based on Original Features')
fig.show()


In [16]:
import plotly.express as px
from sklearn.decomposition import PCA
from sklearn.cluster import KMeans

# Assuming model is already trained and you have the test set X_real_test_scaled
# Get the output probabilities for the test set
y_pred_prob = model.predict(X_real_test_scaled)

# Apply PCA to reduce the dimensionality of the output probabilities to 2D
pca = PCA(n_components=2, random_state=42)
y_pred_embedded = pca.fit_transform(y_pred_prob)

# Perform K-Means clustering on the PCA-reduced data
kmeans = KMeans(n_clusters=5, random_state=42)  # Adjust the number of clusters as needed
clusters = kmeans.fit_predict(y_pred_embedded)

# Create a DataFrame with the embedded points and genre labels
pca_df = pd.DataFrame({
    'PCA Dimension 1': y_pred_embedded[:, 0],
    'PCA Dimension 2': y_pred_embedded[:, 1],
    'Genre': [le_genre.inverse_transform([label])[0] for label in y_real_test.argmax(axis=1)],
    'Track Name': df.loc[X_real_test.index, 'track_name'].values,
    'Cluster': clusters
})

pca_df['Cluster'] = pca_df['Cluster'].astype(str)

# Create an interactive scatter plot with hover information using Plotly Express
fig = px.scatter(pca_df, x='PCA Dimension 1', y='PCA Dimension 2', color='Cluster', hover_data=['Genre', 'Track Name'])
fig.update_layout(title='PCA Visualization of Music Genre Predictions with Clusters')
fig.show()

pca_df

282/282 [==============================] - 1s 2ms/step


/usr/local/lib/python3.10/dist-packages/sklearn/cluster/_kmeans.py:870: FutureWarning:

The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning



PCA Dimension 1  PCA Dimension 2       Genre  \
0           -0.398256         0.136899     Hip-Hop   
1           -0.437196         0.171099         Rap   
2           -0.454805         0.183362     Hip-Hop   
3            0.501972        -0.236892       Anime   
4           -0.064641        -0.120586     Country   
...               ...              ...         ...   
8999        -0.157451        -0.056258     Country   
9000         0.463130        -0.230030       Anime   
9001        -0.380051         0.123697  Electronic   
9002         0.117177        -0.146413     Country   
9003        -0.407625         0.141422         Rap   

                                           Track Name Cluster  
0                                              Swerve       3  
1                                        No One Knows       3  
2     Bedtime Stories (feat. The Weeknd) - From SR3MM       3  
3                                     Polygon Teacher       0  
4                                      Cadillac Style       1  
...                                               ...     ...  
8999                                             Sway       1  
9000                                               21       0  
9001                                   No Coming Down       3  
9002                                   Love Remembers       4  
9003   Swagga Like Us (feat. Kanye West & Lil' Wayne)       3  

[9004 rows x 5 columns]